<a href="https://colab.research.google.com/github/bholeneha/Text_Classification/blob/Fatima/Text_Classification.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
import warnings; warnings.simplefilter('ignore')

# New Section

In [3]:
import numpy as np 
import os
import matplotlib.pyplot as plt
import seaborn as sns
import pandas as pd
import regex
#from wordcloud import WordCloud
from nltk.corpus import stopwords 
from nltk.tokenize import WordPunctTokenizer
from string import punctuation
from nltk.stem import WordNetLemmatizer
import nltk
nltk.download('stopwords')
nltk.download('wordnet')
nltk.download('punkt')
nltk.download('averaged_perceptron_tagger')

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Unzipping corpora/wordnet.zip.
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /root/nltk_data...
[nltk_data]   Unzipping taggers/averaged_perceptron_tagger.zip.


True

In [4]:
names = []
base = 'sample_data/Data/'
with os.scandir(base) as entries:
    for entry in entries:
        if(entry.is_file() == False):
            names.append(entry.name)

try:
  names.remove(".ipynb_checkpoints")
except:
  pass
names

['Entertainment', 'Crime', 'Politics', 'Science']

In [5]:
files = {}
unique = []
for name in names:
    path = base + name+'/'
    x = []
    with os.scandir(path) as entries:
        for entry in entries:
            if(entry.is_file()):
                x.append(entry.name)
    files[name] = x
    files[name].sort()

In [6]:
for k, v in files.items():
    print(k, len(v))

Entertainment 130
Crime 130
Politics 130
Science 130


In [7]:
for i in range(len(names)):
    x = files[names[i]]
    for j in x:
        for k in range(i+1, len(names)):
            key = names[k]
            if j in files[key]:
                files[key].remove(j)

In [8]:
for k, v in files.items():
    print(k, len(v))

Entertainment 130
Crime 0
Politics 130
Science 0


In [9]:
data_LDA = {}
i = 0

for genre in files.keys() :
    texts = files[genre]
    for text in texts:
        if text in files[genre]:
            path = base + genre + '/' + text
            with open(path, "r", encoding = "latin1") as file:
                data_LDA[i] = file.readlines()
                i = i+1
            data_LDA[i-1] = [" ".join(data_LDA[i-1]), genre] 

data_LDA = pd.DataFrame(data_LDA).T
print(data_LDA.shape)
data_LDA.columns = ['Text', 'Class']
data_LDA.head()

(260, 2)


Text          Class
0  \n Archive-name: ripem/faq\n Last-update: Sun,...  Entertainment
1  Approved: news-answers-request@MIT.EDU\n Conte...  Entertainment
2  Approved: news-answers-request@MIT.EDU\n Conte...  Entertainment
3  Message-ID: <1ppvai$l79@bilbo.suite.com>\n Rep...  Entertainment
4  \n    Some sick part of me really liked that p...  Entertainment

In [10]:
data_LDA.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 260 entries, 0 to 259
Data columns (total 2 columns):
 #   Column  Non-Null Count  Dtype 
---  ------  --------------  ----- 
 0   Text    260 non-null    object
 1   Class   260 non-null    object
dtypes: object(2)
memory usage: 6.1+ KB


In [11]:
unique = list(data_LDA.Text.unique())
len(unique)

259

In [12]:
dic = dict(data_LDA)

In [13]:
uni = {}
i = 0
for k in range(len(list(dic['Text']))):
    if dic['Text'][k] in unique:
        uni[i] = [dic['Text'][k], dic['Class'][k]]
        unique.remove(dic['Text'][k])
        i += 1

In [14]:
data_LDA = pd.DataFrame(uni).T
print(data_LDA.shape)
data_LDA.columns = ['Text', 'Class']
data_LDA.head()

(259, 2)


Text          Class
0  \n Archive-name: ripem/faq\n Last-update: Sun,...  Entertainment
1  Approved: news-answers-request@MIT.EDU\n Conte...  Entertainment
2  Approved: news-answers-request@MIT.EDU\n Conte...  Entertainment
3  Message-ID: <1ppvai$l79@bilbo.suite.com>\n Rep...  Entertainment
4  \n    Some sick part of me really liked that p...  Entertainment

In [15]:
def make_wordcloud(words,title):
    cloud = WordCloud(width=1920, height=1080,max_font_size=200, max_words=300, background_color="white").generate(words)
    plt.figure(figsize=(20,20))
    plt.imshow(cloud, interpolation="gaussian")
    plt.axis("off") 
    plt.title(title, fontsize=60)
    plt.show()

In [16]:
wordnet_lemmatizer = WordNetLemmatizer()

stop = stopwords.words('english')

for punct in punctuation:
    stop.append(punct)

def filter_text(text, stop_words):
    word_tokens = WordPunctTokenizer().tokenize(text.lower())
    filtered_text = [regex.sub(u'\p{^Latin}', u'', w) for w in word_tokens if w.isalpha() and len(w) > 3]
    filtered_text = [wordnet_lemmatizer.lemmatize(w, pos="v") for w in filtered_text if not w in stop_words] 
    return " ".join(filtered_text)

In [17]:
data_LDA["filtered_text"] = data_LDA.Text.apply(lambda x : filter_text(x, stop)) 
data_LDA.head()

Text  ...                                      filtered_text
0  \n Archive-name: ripem/faq\n Last-update: Sun,...  ...  archive name ripem last update post still rath...
1  Approved: news-answers-request@MIT.EDU\n Conte...  ...  approve news answer request content type text ...
2  Approved: news-answers-request@MIT.EDU\n Conte...  ...  approve news answer request content type text ...
3  Message-ID: <1ppvai$l79@bilbo.suite.com>\n Rep...  ...  message bilbo suite reply miller suite nntp po...
4  \n    Some sick part of me really liked that p...  ...  sick part really like phrase actually merely t...

[5 rows x 3 columns]

In [18]:
#list(set(data["filtered_text"][0].split(" ")))

#word_list = [text.split(" ") for text in data["filtered_text"]]

word_list = []
for text in data_LDA["filtered_text"]:
    temp = text.split(" ")
    word_list.append(temp)
    
    # for word in temp:
  #     if word not in word_list:
   #        word_list.append(word)
    
print(word_list)

[['archive', 'name', 'ripem', 'last', 'update', 'post', 'still', 'rather', 'rough', 'list', 'likely', 'question', 'information', 'ripem', 'program', 'public', 'mail', 'encryption', 'ripem', 'write', 'maintain', 'marc', 'vanheyningen', 'mvanheyn', 'whale', 'indiana', 'post', 'variety', 'newsgroups', 'monthly', 'basis', 'follow', 'discussion', 'specific', 'ripem', 'redirect', 'group', 'security', 'ripem', 'month', 'reformatted', 'post', 'attempt', 'comply', 'standards', 'hypertext', 'format', 'allow', 'easy', 'manipulation', 'document', 'world', 'wide', 'know', 'think', 'disclaimer', 'nothing', 'consider', 'legal', 'advice', 'anything', 'person', 'opinion', 'want', 'real', 'legal', 'advice', 'talk', 'real', 'lawyer', 'question', 'answer', 'ripem', 'ripem', 'program', 'perform', 'privacy', 'enhance', 'mail', 'use', 'cryptographic', 'techniques', 'allow', 'electronic', 'mail', 'properties', 'authentication', 'send', 'confirm', 'privacy', 'nobody', 'read', 'except', 'intend', 'recipient', '

In [19]:
import gensim
from gensim.utils import simple_preprocess
import nltk
nltk.download('stopwords')
from nltk.corpus import stopwords

import gensim.corpora as corpora

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [39]:
type(word_list[0])

list

In [20]:
# Create Dictionary 
id2word = corpora.Dictionary(word_list)

#print(id2word)

#dictionary = corpora.Dictionary([tokens])
#  print(dictionary)
    
# Create Corpus
texts = word_list

# Term Document Frequency
#corpus = id2word.doc2bow([word_list])
corpus = [id2word.doc2bow(text) for text in texts]
# View
print(corpus)

[[(0, 2), (1, 1), (2, 1), (3, 1), (4, 1), (5, 1), (6, 2), (7, 1), (8, 2), (9, 2), (10, 2), (11, 7), (12, 2), (13, 2), (14, 1), (15, 2), (16, 1), (17, 1), (18, 1), (19, 2), (20, 2), (21, 1), (22, 1), (23, 1), (24, 1), (25, 1), (26, 1), (27, 1), (28, 1), (29, 2), (30, 3), (31, 2), (32, 3), (33, 4), (34, 2), (35, 1), (36, 1), (37, 1), (38, 1), (39, 1), (40, 1), (41, 1), (42, 1), (43, 2), (44, 1), (45, 1), (46, 1), (47, 2), (48, 5), (49, 2), (50, 1), (51, 1), (52, 1), (53, 1), (54, 1), (55, 1), (56, 1), (57, 3), (58, 3), (59, 3), (60, 1), (61, 1), (62, 1), (63, 3), (64, 3), (65, 1), (66, 1), (67, 4), (68, 1), (69, 1), (70, 1), (71, 1), (72, 1), (73, 1), (74, 1), (75, 3), (76, 1), (77, 1), (78, 4), (79, 3), (80, 1), (81, 1), (82, 1), (83, 1), (84, 1), (85, 1), (86, 1), (87, 1), (88, 1), (89, 1), (90, 1), (91, 3), (92, 2), (93, 4), (94, 2), (95, 5), (96, 4), (97, 1), (98, 1), (99, 1), (100, 1), (101, 5), (102, 1), (103, 2), (104, 2), (105, 1), (106, 1), (107, 1), (108, 2), (109, 2), (110, 1)

In [21]:
###training LDA model

from pprint import pprint
# number of topics
num_topics = 4
# Build LDA model
lda_model = gensim.models.LdaMulticore(corpus=corpus,
                                       id2word=id2word,
                                       num_topics=num_topics)
# Print the Keyword in the 5 topics
pprint(lda_model.print_topics())
doc_lda = lda_model[corpus]

[(0,
  '0.009*"encryption" + 0.006*"privacy" + 0.006*"use" + 0.005*"information" + '
  '0.005*"file" + 0.005*"public" + 0.004*"security" + 0.004*"system" + '
  '0.004*"post" + 0.004*"internet"'),
 (1,
  '0.007*"would" + 0.006*"post" + 0.006*"use" + 0.005*"public" + '
  '0.004*"message" + 0.004*"make" + 0.004*"write" + 0.004*"anonymous" + '
  '0.004*"know" + 0.003*"security"'),
 (2,
  '0.005*"people" + 0.005*"use" + 0.005*"right" + 0.005*"encryption" + '
  '0.005*"write" + 0.004*"make" + 0.004*"would" + 0.004*"government" + '
  '0.004*"article" + 0.004*"post"'),
 (3,
  '0.005*"would" + 0.005*"people" + 0.005*"write" + 0.005*"encryption" + '
  '0.004*"privacy" + 0.004*"make" + 0.004*"right" + 0.004*"post" + '
  '0.004*"like" + 0.003*"use"')]


In [22]:
!pip install pyLDAvis==2.1.2

     |████████████████████████████████| 1.6MB 6.7MB/s 
  Created wheel for pyLDAvis: filename=pyLDAvis-2.1.2-py2.py3-none-any.whl size=97712 sha256=a09ab1323289c451c0946a32260a6c9de4b588c4ff141f2b6a0ff2119036d37a
  Stored in directory: /root/.cache/pip/wheels/98/71/24/513a99e58bb6b8465bae4d2d5e9dba8f0bef8179e3051ac414
Successfully built pyLDAvis


In [23]:
import pyLDAvis.gensim
pyLDAvis.enable_notebook()
vis = pyLDAvis.gensim.prepare(lda_model, corpus, dictionary=lda_model.id2word)
vis

/usr/local/lib/python3.7/dist-packages/past/types/oldstr.py:5: DeprecationWarning: Using or importing the ABCs from 'collections' instead of from 'collections.abc' is deprecated since Python 3.3,and in 3.9 it will stop working
  from collections import Iterable


PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
1      0.003527  0.014478       1        1  31.490669
0     -0.018290 -0.003973       2        1  31.156939
3     -0.000984 -0.002492       3        1  25.044164
2      0.015747 -0.008013       4        1  12.308228, topic_info=             Term        Freq       Total Category  logprob  loglift
286        people  236.000000  236.000000  Default  30.0000  30.0000
125    encryption  360.000000  360.000000  Default  29.0000  29.0000
1161         byte   57.000000   57.000000  Default  28.0000  28.0000
574         right  224.000000  224.000000  Default  27.0000  27.0000
616         would  315.000000  315.000000  Default  26.0000  26.0000
...           ...         ...         ...      ...      ...      ...
317        public   19.846510  258.611410   Topic4  -6.0036  -0.4724
307       privacy   19.064637  277.693720   Topic4  -6.0438  -0.5838
766         state   17.157056  157.232099   Topic4  -6.1492  -0.1204
95           data   16.607591  157.966922   Topic4  -6.1817  -0.1576
186   information   16.699275  222.194804   Topic4  -6.1762  -0.4933

[362 rows x 6 columns], token_table=      Topic      Freq     Term
term                          
8031      3  0.812726    abort
6930      3  0.600523  acronym
450       1  0.409885  address
450       2  0.299916  address
450       3  0.209941  address
...     ...       ...      ...
445       4  0.140080    write
1093      1  0.450439    years
1093      2  0.200195    years
1093      3  0.250244    years
1093      4  0.100098    years

[766 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[2, 1, 4, 3])

In [ ]:
#### Useful insights into the data set by constructing wordclouds and find term frequencies in each topic (Topic=4)

In [39]:

from wordcloud import WordCloud

In [40]:
all_text = " ".join(data_LDA[data_LDA.Class == "Crime"].filtered_text) 
make_wordcloud(all_text, "Crime")

ValueError: ignored

In [29]:
count = pd.DataFrame(all_text.split(), columns = ['words'])
top_10 = count[count['words'].isin(list(count.words.value_counts()[:20].index[:20]))]
plt.figure(figsize=(20,5))
sns.barplot(x = top_10.words.value_counts().index,
            y = top_10.words.value_counts(), palette = sns.color_palette("mako"))

ValueError: ignored

<Figure size 1440x360 with 0 Axes>

In [ ]:
###Applying NNs to individual classes and for that first we create seperate data frames for each class
#import pandas as pd
#df = pd.read_csv('file_location\filename.txt', delimiter = "\t")

In [26]:
files = {}
unique = []
for name in names:
    path = base + name+'/'
    x = []
    with os.scandir(path) as entries:
        for entry in entries:
            if(entry.is_file()):
                x.append(entry.name)
    files[name] = x
    files[name].sort()

In [27]:
for k, v in files.items():
    print(k, len(v))

Entertainment 130
Crime 130
Politics 130
Science 130


In [28]:
data = {}
i = 0

for genre in files.keys() :
    texts = files[genre]
    for text in texts:
        if text in files[genre]:
            path = base + genre + '/' + text
            with open(path, "r", encoding = "latin1") as file:
                data[i] = file.readlines()
                i = i+1
            data[i-1] = [" ".join(data[i-1]), genre] 
#data
data = pd.DataFrame(data).T
print(data.shape)
data.columns = ['Text', 'Class']
data

(520, 2)


Text          Class
0    \n Archive-name: ripem/faq\n Last-update: Sun,...  Entertainment
1    Approved: news-answers-request@MIT.EDU\n Conte...  Entertainment
2    Approved: news-answers-request@MIT.EDU\n Conte...  Entertainment
3    Message-ID: <1ppvai$l79@bilbo.suite.com>\n Rep...  Entertainment
4    \n    Some sick part of me really liked that p...  Entertainment
..                                                 ...            ...
515  \n In article <1qnmnp$db8@sol.TIS.COM> mjr@tis...        Science
516  Distribution: inet\n Message-ID: <1qoapv$9rn@l...        Science
517  NNTP-Posting-Host: sayshell.umd.edu\n \n In ar...        Science
518  \n In article <1993Apr16.165423.27204@linus.mi...        Science
519  \n In article <rlglendeC5LrwC.95C@netcom.com>,...        Science

[520 rows x 2 columns]

In [29]:
data["Class"].unique()

array(['Entertainment', 'Crime', 'Politics', 'Science'], dtype=object)

In [30]:
### Develop four seperate dataframes
crime_df=data.loc[data['Class']=="Crime"]
politics_df=data.loc[data['Class']=="Politics"]
science_df=data.loc[data['Class']=="Science"]
entertainment_df=data.loc[data['Class']=="Entertainment"]

In [32]:
####Multi-lable Text Classification Model with Single Output Layer
data.head()

Text          Class
0  \n Archive-name: ripem/faq\n Last-update: Sun,...  Entertainment
1  Approved: news-answers-request@MIT.EDU\n Conte...  Entertainment
2  Approved: news-answers-request@MIT.EDU\n Conte...  Entertainment
3  Message-ID: <1ppvai$l79@bilbo.suite.com>\n Rep...  Entertainment
4  \n    Some sick part of me really liked that p...  Entertainment

In [41]:
wordnet_lemmatizer = WordNetLemmatizer()

stop = stopwords.words('english')

for punct in punctuation:
    stop.append(punct)

def filter_text(text, stop_words):
    word_tokens = WordPunctTokenizer().tokenize(text.lower())
    filtered_text = [regex.sub(u'\p{^Latin}', u'', w) for w in word_tokens if w.isalpha() and len(w) > 3]
    filtered_text = [wordnet_lemmatizer.lemmatize(w, pos="v") for w in filtered_text if not w in stop_words] 
    return " ".join(filtered_text)

<input>:10: DeprecationWarning: invalid escape sequence \p
<input>:10: DeprecationWarning: invalid escape sequence \p
<input>:10: DeprecationWarning: invalid escape sequence \p
<ipython-input-41-bda860dea417>:10: DeprecationWarning: invalid escape sequence \p
  filtered_text = [regex.sub(u'\p{^Latin}', u'', w) for w in word_tokens if w.isalpha() and len(w) > 3]


In [42]:
data["filtered_text"] = data.Text.apply(lambda x : filter_text(x, stop)) 
data.head()

Text  ...                                      filtered_text
0  \n Archive-name: ripem/faq\n Last-update: Sun,...  ...  archive name ripem last update post still rath...
1  Approved: news-answers-request@MIT.EDU\n Conte...  ...  approve news answer request content type text ...
2  Approved: news-answers-request@MIT.EDU\n Conte...  ...  approve news answer request content type text ...
3  Message-ID: <1ppvai$l79@bilbo.suite.com>\n Rep...  ...  message bilbo suite reply miller suite nntp po...
4  \n    Some sick part of me really liked that p...  ...  sick part really like phrase actually merely t...

[5 rows x 3 columns]

In [45]:
#list(set(data["filtered_text"][0].split(" ")))

#word_list = [text.split(" ") for text in data["filtered_text"]]

word_list = []
for text in data["filtered_text"]:
    temp = text.split(" ")
    word_list.append(temp)
    
    # for word in temp:
  #     if word not in word_list:
   #        word_list.append(word)
    
print(word_list)

[['archive', 'name', 'ripem', 'last', 'update', 'post', 'still', 'rather', 'rough', 'list', 'likely', 'question', 'information', 'ripem', 'program', 'public', 'mail', 'encryption', 'ripem', 'write', 'maintain', 'marc', 'vanheyningen', 'mvanheyn', 'whale', 'indiana', 'post', 'variety', 'newsgroups', 'monthly', 'basis', 'follow', 'discussion', 'specific', 'ripem', 'redirect', 'group', 'security', 'ripem', 'month', 'reformatted', 'post', 'attempt', 'comply', 'standards', 'hypertext', 'format', 'allow', 'easy', 'manipulation', 'document', 'world', 'wide', 'know', 'think', 'disclaimer', 'nothing', 'consider', 'legal', 'advice', 'anything', 'person', 'opinion', 'want', 'real', 'legal', 'advice', 'talk', 'real', 'lawyer', 'question', 'answer', 'ripem', 'ripem', 'program', 'perform', 'privacy', 'enhance', 'mail', 'use', 'cryptographic', 'techniques', 'allow', 'electronic', 'mail', 'properties', 'authentication', 'send', 'confirm', 'privacy', 'nobody', 'read', 'except', 'intend', 'recipient', '

In [46]:
import gensim
from gensim.utils import simple_preprocess
import nltk
nltk.download('stopwords')
from nltk.corpus import stopwords

import gensim.corpora as corpora

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [47]:
# Create Dictionary 
id2word = corpora.Dictionary(word_list)

#print(id2word)

#dictionary = corpora.Dictionary([tokens])
#  print(dictionary)
    
# Create Corpus
texts = word_list

# Term Document Frequency
#corpus = id2word.doc2bow([word_list])
corpus = [id2word.doc2bow(text) for text in texts]
# View
print(corpus)

[[(0, 2), (1, 1), (2, 1), (3, 1), (4, 1), (5, 1), (6, 2), (7, 1), (8, 2), (9, 2), (10, 2), (11, 7), (12, 2), (13, 2), (14, 1), (15, 2), (16, 1), (17, 1), (18, 1), (19, 2), (20, 2), (21, 1), (22, 1), (23, 1), (24, 1), (25, 1), (26, 1), (27, 1), (28, 1), (29, 2), (30, 3), (31, 2), (32, 3), (33, 4), (34, 2), (35, 1), (36, 1), (37, 1), (38, 1), (39, 1), (40, 1), (41, 1), (42, 1), (43, 2), (44, 1), (45, 1), (46, 1), (47, 2), (48, 5), (49, 2), (50, 1), (51, 1), (52, 1), (53, 1), (54, 1), (55, 1), (56, 1), (57, 3), (58, 3), (59, 3), (60, 1), (61, 1), (62, 1), (63, 3), (64, 3), (65, 1), (66, 1), (67, 4), (68, 1), (69, 1), (70, 1), (71, 1), (72, 1), (73, 1), (74, 1), (75, 3), (76, 1), (77, 1), (78, 4), (79, 3), (80, 1), (81, 1), (82, 1), (83, 1), (84, 1), (85, 1), (86, 1), (87, 1), (88, 1), (89, 1), (90, 1), (91, 3), (92, 2), (93, 4), (94, 2), (95, 5), (96, 4), (97, 1), (98, 1), (99, 1), (100, 1), (101, 5), (102, 1), (103, 2), (104, 2), (105, 1), (106, 1), (107, 1), (108, 2), (109, 2), (110, 1)

In [49]:
###### X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.20, random_state=42), for splitting, we assign X and y
X=corpus
X

[[(0, 2),
  (1, 1),
  (2, 1),
  (3, 1),
  (4, 1),
  (5, 1),
  (6, 2),
  (7, 1),
  (8, 2),
  (9, 2),
  (10, 2),
  (11, 7),
  (12, 2),
  (13, 2),
  (14, 1),
  (15, 2),
  (16, 1),
  (17, 1),
  (18, 1),
  (19, 2),
  (20, 2),
  (21, 1),
  (22, 1),
  (23, 1),
  (24, 1),
  (25, 1),
  (26, 1),
  (27, 1),
  (28, 1),
  (29, 2),
  (30, 3),
  (31, 2),
  (32, 3),
  (33, 4),
  (34, 2),
  (35, 1),
  (36, 1),
  (37, 1),
  (38, 1),
  (39, 1),
  (40, 1),
  (41, 1),
  (42, 1),
  (43, 2),
  (44, 1),
  (45, 1),
  (46, 1),
  (47, 2),
  (48, 5),
  (49, 2),
  (50, 1),
  (51, 1),
  (52, 1),
  (53, 1),
  (54, 1),
  (55, 1),
  (56, 1),
  (57, 3),
  (58, 3),
  (59, 3),
  (60, 1),
  (61, 1),
  (62, 1),
  (63, 3),
  (64, 3),
  (65, 1),
  (66, 1),
  (67, 4),
  (68, 1),
  (69, 1),
  (70, 1),
  (71, 1),
  (72, 1),
  (73, 1),
  (74, 1),
  (75, 3),
  (76, 1),
  (77, 1),
  (78, 4),
  (79, 3),
  (80, 1),
  (81, 1),
  (82, 1),
  (83, 1),
  (84, 1),
  (85, 1),
  (86, 1),
  (87, 1),
  (88, 1),
  (89, 1),
  (90, 1),
  (91, 3)

In [43]:
X = data["filtered_text"]
X

0      archive name ripem last update post still rath...
1      approve news answer request content type text ...
2      approve news answer request content type text ...
3      message bilbo suite reply miller suite nntp po...
4      sick part really like phrase actually merely t...
                             ...                        
515    article marcus ranum write traffic traffic loo...
516    distribution inet message lucy reference dive ...
517    nntp post host sayshell article netcom tcmay n...
518    article linus mitre ptrei bistromath mitre pet...
519    article netcom rlglende netcom robert lewis gl...
Name: filtered_text, Length: 520, dtype: object

In [44]:
y=data

In [37]:
###### DO WE REALLY HAVE TO DO IT AS they are doing bag of words after splitting into test and train

###divide our data into training and test sets:  
from numpy import array
from keras.preprocessing.text import one_hot
from keras.preprocessing.sequence import pad_sequences
from keras.models import Sequential
from keras.layers.core import Activation, Dropout, Dense
from keras.layers import Flatten, LSTM
from keras.layers import GlobalMaxPooling1D
from keras.models import Model
from keras.layers.embeddings import Embedding
from sklearn.model_selection import train_test_split
from keras.preprocessing.text import Tokenizer
from keras.layers import Input
from keras.layers.merge import Concatenate

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.20, random_state=42)